In [1]:
import pandas as pd
from Linguistic_Features import*
import nltk
from nltk.tokenize import word_tokenize

In [2]:
Folder_Path = "/Users/pranjali/Downloads/Wiki_BiasDetection/Data/Task2_FinalData/"

Subjective_Data = pd.read_csv(Folder_Path+"WikiEdits_Subjective.tsv", sep="\t")
Objective_Data = pd.read_csv(Folder_Path+"WikiEdits_Objective.tsv", sep="\t")

print(Subjective_Data.shape)
print(Objective_Data.shape)

(181472, 8)
(385526, 6)


In [3]:
## Filter Subjective data : Keep sentences with single word edit only

Filtered_Data = []

for i in range(Subjective_Data.shape[0]):
    
    row = Subjective_Data.iloc[i]
        
    src_sentence = row['Src_Raw']
    target_sentence = row['Target_Raw']
    
    src_sent_words = word_tokenize(src_sentence)
    src_sent_words = [w for w in src_sent_words if w.isalpha()]
    
    target_sent_words = word_tokenize(target_sentence)
    target_sent_words = [w for w in target_sent_words if w.isalpha()]
    
    diff = len(src_sent_words) - len(target_sent_words)
    
    if abs(diff) < 2:
        Filtered_Data.append([src_sentence, target_sentence])
        
Filtered_Data_DF = pd.DataFrame(Filtered_Data, columns=['Src_Sent', 'Target_Sent'])

print(Filtered_Data_DF.shape)
print(Filtered_Data_DF.head())

(93321, 2)
                                            Src_Sent  \
0  nicaea was convoked by the emperor constantine...   
1  dennis the menace is an american animated seri...   
2  today, on large farms, motorcycles, dogs or me...   
3  the fifteenth united states army was the last ...   
4  a massive toxic spill occurs at gold king mine...   

                                         Target_Sent  
0  nicaea was convoked by the emperor constantine...  
1  dennis the menace is an american animated seri...  
2  today, on large farms, motorcycles, dogs or pe...  
3  the fifteenth united states army was the last ...  
4  a toxic spill occurs at gold king mine near du...  


In [2]:
## Create new data where, linguistic features for words from each sentence in above filtered data are computed 
## and label is assigned to the word 1-->edited (Subjective), 0-->not edited (Objective)

## This data may contain multiple entries for same word beacause same word can have different linguistic features 
## in different contexts/sentences. Also, same word might be assigned different labels in different contexts.

ColumnList = ["word", "lemma", "POS", "POS_Prev", "POS_Next", "Sent_Position", 
                  "Hedge", "Hedge_Context", "Factive", "Factive_Context", "Assertive", "Assertive_Context",
                  "Implicative", "Implicative_Context", "Report", "Report_Context", 
                   "Entailment", "Entailment_Context", "StrongSub", "StrongSub_Context", 
                   "WeakSub", "WeakSub_Context", "Polarity", "Positive", "Positive_Context", 
                   "Negative", "Negative_Context", "Bias_Lexicon", "Label"]

## Get linguistic features for all words in the sentence
## and assign appropriate label to each word
def Sent_Features_Label(src_sentence, target_sentence):
    
    src_sent_words = word_tokenize(src_sentence)
    src_sent_words = [w for w in src_sent_words if w.isalpha()]

    target_sent_words = word_tokenize(target_sentence)
    target_sent_words = [w for w in target_sent_words if w.isalpha()]
    
    print(src_sentence)
    Sent_Linguistic_Features = Get_Sent_Linguistic_Features(src_sentence)
    Target_Linguistic_Features = Get_Sent_Linguistic_Features(target_sentence)

    Sentence_Feature_label = []

    for j in range(len(src_sent_words)):

        src_sent_word = src_sent_words[j]
        word_features = list(Sent_Linguistic_Features.iloc[j])

        context_start = max(j-1, 0)
        context_end = min(len(target_sent_words), j+1)

        Target_sent_context = target_sent_words[context_start:context_end+1]

        if src_sent_word in Target_sent_context:
            word_features.append('0')
        else:
            word_features.append('1')

        Sentence_Feature_label.append(word_features)
        
    Sentence_Feature_label_DF = pd.DataFrame(Sentence_Feature_label, columns=ColumnList)
    
    return Sentence_Feature_label_DF

## Get dataframe containing feature_label vector for each word in it for each sentence
## Concat dataframes of all sentences into one dataframe
def Create_Dataset(data):
    
    Sentences_DF = pd.DataFrame(columns=ColumnList)
    
    for i in range(data.shape[0]):
        
        row = data.iloc[i]
        
        src_sentence = row['Src_Sent']
        target_sentence = row['Target_Sent']
        
        Sent_DF = Sent_Features_Label(src_sentence, target_sentence)
        Sentences_DF = pd.concat([Sentences_DF, Sent_DF])
    
    return Sentences_DF

In [4]:
Sentences_DF = Create_Dataset(Filtered_Data_DF)

the nintendo ds (which is short for dual screen, although nintendo has also promotionally said it to be short for developer's system, due to their claim of the "sheer joy" of developing games for the handheld), is a dual-screen portable handheld game console developed and manufactured by nintendo.
[('the', 'DT'), ('nintendo', 'JJ'), ('ds', 'NN'), ('which', 'WDT'), ('is', 'VBZ'), ('short', 'JJ'), ('for', 'IN'), ('dual', 'JJ'), ('screen', 'NN'), ('although', 'IN'), ('nintendo', 'NN'), ('has', 'VBZ'), ('also', 'RB'), ('promotionally', 'RB'), ('said', 'VBD'), ('it', 'PRP'), ('to', 'TO'), ('be', 'VB'), ('short', 'JJ'), ('for', 'IN'), ('developer', 'NN'), ('system', 'NN'), ('due', 'JJ'), ('to', 'TO'), ('their', 'PRP$'), ('claim', 'NN'), ('of', 'IN'), ('the', 'DT'), ('sheer', 'NN'), ('joy', 'NN'), ('of', 'IN'), ('developing', 'VBG'), ('games', 'NNS'), ('for', 'IN'), ('the', 'DT'), ('handheld', 'NN'), ('is', 'VBZ'), ('a', 'DT'), ('portable', 'JJ'), ('handheld', 'JJ'), ('game', 'NN'), ('console

odex's subtitling has been criticised by fans of anime for having an ugly font and sometimes inaccurate translations, compared to fansubs or imports.
[('odex', 'NN'), ('subtitling', 'NN'), ('has', 'VBZ'), ('been', 'VBN'), ('criticised', 'VBN'), ('by', 'IN'), ('fans', 'NNS'), ('of', 'IN'), ('anime', 'NN'), ('for', 'IN'), ('having', 'VBG'), ('an', 'DT'), ('ugly', 'JJ'), ('font', 'NN'), ('and', 'CC'), ('sometimes', 'RB'), ('inaccurate', 'JJ'), ('translations', 'NNS'), ('compared', 'VBN'), ('to', 'TO'), ('fansubs', 'VB'), ('or', 'CC'), ('imports', 'NNS')]
[('odex', 'NN'), ('subtitling', 'NN'), ('has', 'VBZ'), ('been', 'VBN'), ('criticised', 'VBN'), ('by', 'IN'), ('fans', 'NNS'), ('of', 'IN'), ('anime', 'NN'), ('for', 'IN'), ('having', 'VBG'), ('an', 'DT'), ('less', 'JJR'), ('quality', 'JJ'), ('font', 'NN'), ('and', 'CC'), ('sometimes', 'RB'), ('inaccurate', 'JJ'), ('translations', 'NNS'), ('compared', 'VBN'), ('to', 'TO'), ('fansubs', 'VB'), ('or', 'CC'), ('imports', 'NNS')]
corrine grant:

alternative varieties taking roughly the same amount of time as early girl include sasha's altai and stupice .
[('alternative', 'JJ'), ('varieties', 'NNS'), ('taking', 'VBG'), ('roughly', 'RB'), ('the', 'DT'), ('same', 'JJ'), ('amount', 'NN'), ('of', 'IN'), ('time', 'NN'), ('as', 'IN'), ('early', 'JJ'), ('girl', 'NN'), ('include', 'VBP'), ('sasha', 'NN'), ('altai', 'NN'), ('and', 'CC'), ('stupice', 'NN')]
[('alternatives', 'NNS'), ('that', 'WDT'), ('take', 'VBP'), ('roughly', 'RB'), ('the', 'DT'), ('same', 'JJ'), ('amount', 'NN'), ('of', 'IN'), ('time', 'NN'), ('as', 'IN'), ('early', 'JJ'), ('girl', 'NN'), ('include', 'VBP'), ('sasha', 'NN'), ('altai', 'NN'), ('and', 'CC'), ('stupice', 'NN')]
the 17th century was rich in popular risings, such as the liberation of moscow from the polish invaders (1612), the salt riot (1648), the copper riot (1662), and the moscow uprising of 1682. the city ceased to be russia's capital in 1703, after founding st. petersburg by peter the great on the bal

his famous recording of carmina burana is considered by most to be the authoritative interpretation, as orff himself was present at the rehearsals and condoned the final performance.
[('his', 'PRP$'), ('famous', 'JJ'), ('recording', 'NN'), ('of', 'IN'), ('carmina', 'NN'), ('burana', 'NN'), ('is', 'VBZ'), ('considered', 'VBN'), ('by', 'IN'), ('most', 'JJS'), ('to', 'TO'), ('be', 'VB'), ('the', 'DT'), ('authoritative', 'JJ'), ('interpretation', 'NN'), ('as', 'IN'), ('orff', 'NN'), ('himself', 'PRP'), ('was', 'VBD'), ('present', 'JJ'), ('at', 'IN'), ('the', 'DT'), ('rehearsals', 'NNS'), ('and', 'CC'), ('condoned', 'VBD'), ('the', 'DT'), ('final', 'JJ'), ('performance', 'NN')]
[('his', 'PRP$'), ('recording', 'NN'), ('of', 'IN'), ('carmina', 'NN'), ('burana', 'NN'), ('is', 'VBZ'), ('considered', 'VBN'), ('by', 'IN'), ('some', 'DT'), ('to', 'TO'), ('be', 'VB'), ('an', 'DT'), ('authoritative', 'JJ'), ('interpretation', 'NN'), ('as', 'IN'), ('orff', 'NN'), ('himself', 'PRP'), ('was', 'VBD'), (

in the 1910/11 season although the team sadly lost billy gillespie to leeds city, they managed to reach the semi-final of the irish junior cup, in which they were defeated by broadway united (at the brandywell) by two goals to one.
[('in', 'IN'), ('the', 'DT'), ('season', 'NN'), ('although', 'IN'), ('the', 'DT'), ('team', 'NN'), ('sadly', 'RB'), ('lost', 'VBD'), ('billy', 'RB'), ('gillespie', 'VBN'), ('to', 'TO'), ('leeds', 'NNS'), ('city', 'NN'), ('they', 'PRP'), ('managed', 'VBD'), ('to', 'TO'), ('reach', 'VB'), ('the', 'DT'), ('of', 'IN'), ('the', 'DT'), ('irish', 'JJ'), ('junior', 'JJ'), ('cup', 'NN'), ('in', 'IN'), ('which', 'WDT'), ('they', 'PRP'), ('were', 'VBD'), ('defeated', 'VBN'), ('by', 'IN'), ('broadway', 'NN'), ('united', 'JJ'), ('at', 'IN'), ('the', 'DT'), ('brandywell', 'NN'), ('by', 'IN'), ('two', 'CD'), ('goals', 'NNS'), ('to', 'TO'), ('one', 'CD')]
[('in', 'IN'), ('the', 'DT'), ('season', 'NN'), ('although', 'IN'), ('the', 'DT'), ('team', 'NN'), ('lost', 'VBD'), ('bi

...

17 on the billboard top 200 and selling 18,342 copies in its first week.
[('on', 'IN'), ('the', 'DT'), ('billboard', 'NN'), ('top', 'NN'), ('and', 'CC'), ('selling', 'VBG'), ('copies', 'NNS'), ('in', 'IN'), ('its', 'PRP$'), ('first', 'JJ'), ('week', 'NN')]
[('on', 'IN'), ('the', 'DT'), ('billboard', 'NN'), ('top', 'NN'), ('and', 'CC'), ('sold', 'VBD'), ('copies', 'NNS'), ('in', 'IN'), ('its', 'PRP$'), ('first', 'JJ'), ('week', 'NN')]
mr tay seow huah ( d. september 1980, age 47) was a senior civil servant who served at various times as director of the special branch, director of the security and intelligence division , permanent secretary (home affairs) and permanent secretary (defence), prior to his retirement in 1976. he was awarded the prestigious meritorious service award in 1967, and the eisenhower fellowships in 1971.he was acting permenant secretary of home affairs around 1971 and was involved in the laju incident.
[('mr', 'NN'), ('tay', 'NN'), ('seow', 'NN'), ('huah', 'NN'), ('

iran executes three kurdish men , including ramin panahi, for terrorism offences.
[('iran', 'NN'), ('executes', 'NNS'), ('three', 'CD'), ('kurdish', 'JJ'), ('men', 'NNS'), ('including', 'VBG'), ('ramin', 'NN'), ('panahi', 'NN'), ('for', 'IN'), ('terrorism', 'NN'), ('offences', 'NNS')]
[('iran', 'NN'), ('executes', 'NNS'), ('three', 'CD'), ('kurdish', 'JJ'), ('prisoners', 'NNS'), ('including', 'VBG'), ('ramin', 'NN'), ('panahi', 'NN'), ('for', 'IN'), ('terrorism', 'NN'), ('offences', 'NNS')]
cedric benson attended lee high school in midland, texas, and finished his superb career with 8,423 rushing yards in his career (the most in texas 5a history and the fourth most in texas high school football history).
[('cedric', 'JJ'), ('benson', 'NN'), ('attended', 'VBD'), ('lee', 'JJ'), ('high', 'JJ'), ('school', 'NN'), ('in', 'IN'), ('midland', 'NN'), ('texas', 'NN'), ('and', 'CC'), ('finished', 'VBD'), ('his', 'PRP$'), ('superb', 'JJ'), ('career', 'NN'), ('with', 'IN'), ('rushing', 'VBG'), ('ya

the zayre chain ceased to exist two years later, in 1990, although tjx is still going strong today.
[('the', 'DT'), ('zayre', 'NN'), ('chain', 'NN'), ('ceased', 'VBD'), ('to', 'TO'), ('exist', 'VB'), ('two', 'CD'), ('years', 'NNS'), ('later', 'RB'), ('in', 'IN'), ('although', 'IN'), ('tjx', 'NN'), ('is', 'VBZ'), ('still', 'RB'), ('going', 'VBG'), ('strong', 'JJ'), ('today', 'NN')]
[('the', 'DT'), ('zayre', 'NN'), ('chain', 'NN'), ('ceased', 'VBD'), ('to', 'TO'), ('exist', 'VB'), ('two', 'CD'), ('years', 'NNS'), ('later', 'RB'), ('in', 'IN'), ('although', 'IN'), ('tjx', 'NN'), ('is', 'VBZ'), ('still', 'RB'), ('in', 'IN'), ('operation', 'NN'), ('today', 'NN')]
however, it wasn't long before a defence lawyer involved in the trial revealed that kinsella was working for both cn rail and bc rail in the time before the $1-billion sale of bc rail to cn was finalized.
[('however', 'RB'), ('it', 'PRP'), ('was', 'VBD'), ('long', 'RB'), ('before', 'IN'), ('a', 'DT'), ('defence', 'NN'), ('lawyer', 

william levitt is considered the father of modern suburbia, and levittown being his first community, it is considered by many to be the first modern, postwar american suburb.
[('william', 'NN'), ('levitt', 'NN'), ('is', 'VBZ'), ('considered', 'VBN'), ('the', 'DT'), ('father', 'NN'), ('of', 'IN'), ('modern', 'JJ'), ('suburbia', 'NN'), ('and', 'CC'), ('levittown', 'JJ'), ('being', 'VBG'), ('his', 'PRP$'), ('first', 'JJ'), ('community', 'NN'), ('it', 'PRP'), ('is', 'VBZ'), ('considered', 'VBN'), ('by', 'IN'), ('many', 'JJ'), ('to', 'TO'), ('be', 'VB'), ('the', 'DT'), ('first', 'JJ'), ('modern', 'JJ'), ('postwar', 'JJ'), ('american', 'JJ'), ('suburb', 'NN')]
[('william', 'NN'), ('levitt', 'NN'), ('is', 'VBZ'), ('considered', 'VBN'), ('the', 'DT'), ('father', 'NN'), ('of', 'IN'), ('modern', 'JJ'), ('suburbia', 'NN'), ('and', 'CC'), ('levittown', 'JJ'), ('being', 'VBG'), ('his', 'PRP$'), ('first', 'JJ'), ('community', 'NN'), ('it', 'PRP'), ('is', 'VBZ'), ('considered', 'VBN'), ('by', 'IN'), 

born in inagh, county clare, kelly first excelled at hurling whilst at school in st. flannan's college.
[('born', 'VBN'), ('in', 'IN'), ('inagh', 'NN'), ('county', 'NN'), ('clare', 'NN'), ('kelly', 'RB'), ('first', 'RB'), ('excelled', 'VBN'), ('at', 'IN'), ('hurling', 'VBG'), ('whilst', 'NN'), ('at', 'IN'), ('school', 'NN'), ('in', 'IN'), ('flannan', 'NN'), ('college', 'NN')]
[('born', 'VBN'), ('in', 'IN'), ('inagh', 'NN'), ('county', 'NN'), ('clare', 'NN'), ('kelly', 'RB'), ('first', 'JJ'), ('played', 'VBD'), ('competitive', 'JJ'), ('hurling', 'NN'), ('whilst', 'NN'), ('at', 'IN'), ('school', 'NN'), ('in', 'IN'), ('flannan', 'NN'), ('college', 'NN')]
the most famous of these is dale earnhardt, who died february 18, 2001.
[('the', 'DT'), ('most', 'RBS'), ('famous', 'JJ'), ('of', 'IN'), ('these', 'DT'), ('is', 'VBZ'), ('dale', 'JJ'), ('earnhardt', 'NN'), ('who', 'WP'), ('died', 'VBD'), ('february', 'JJ')]
[('arguably', 'RB'), ('the', 'DT'), ('most', 'RBS'), ('notable', 'JJ'), ('was', 'V

In [16]:
Filtered_Data_DF.to_csv("./Filtered_Data.tsv")

In [3]:
Filtered_Data_DF = pd.read_csv("./Filtered_Data.tsv")

In [5]:
Sentences_DF.to_csv("./WikiEdits_Words_Features.csv", columns=ColumnList)